In [2]:
%matplotlib notebook

import quandl
import pandas as pd
import pickle
import matplotlib.pyplot as plt
from matplotlib import style
style.use('fivethirtyeight')

api_key = 'kgMN5tuNUwb7-F29s6xp' 

In [15]:
def mortgage_30y():
    df = quandl.get("FMAC/MORTG", trim_start="1975-01-01", authtoken=api_key)
    df["Value"] = (df["Value"]-df["Value"][0]) / df["Value"][0] * 100.0
    df=df.resample('1D')
    df=df.resample('M')
    return df


def state_list():
    fiddy_states = pd.read_html('https://simple.wikipedia.org/wiki/List_of_U.S._states') # head html into a list of dataframes
    return fiddy_states[0][0][1:]


def grab_initial_state_data():
    states = state_list()
    main_df = pd.DataFrame()

    for abbv in states:
        query = "FMAC/HPI_"+str(abbv)
        df1 = quandl.get(query, authtoken=api_key)
        
        df1=df1.rename(columns = {'Value': abbv}) #Change Value to State Abbrev
        df1=df1.rename(columns = {'?Date': 'Date'}) # fix a space in front of Date

        #df = df.pct_change() # change data to percent change
        df[abbv] = (df1 - df1.iloc[0]) / df1.iloc[0] * 100 # make it so the numbs start at 0 (New - Old) / old * 100
        #print(df[abbv].head())

        if main_df.empty:
            main_df = df[abbv] # first run make main_df equal to df
        else:
            main_df[abbv] = df[abbv] # add column to main_df

    #print(main_df.head())

#IF YOU USE THIS YOU HAVE TO 'IMPORT PICKLE' AT THE TOP...A FASTER VERSION IS BELOW
    pickle_out = open('fiddy_states3.pickle','wb') # how you setup pickle
    pickle.dump(main_df, pickle_out) # how you save the pickle
    pickle_out.close()
    
    
def HPI_Benchmark():
    df = quandl.get('FMAC/HPI_USA', authtoken=api_key)
    df=df.rename(columns = {'Value': 'United States'}) #Change Value to State Abbrev
    df=df.rename(columns = {'?Date': 'Date'}) # fix a space in front of Date
    df = (df["United States"] - df["United States"][0]) / df["United States"][0] * 100.0
    return df
    

    
HPI_data = pd.read_pickle('fiddy_states3.pickle')
m30 = mortgage_30y()
HPI_Bench = HPI_Benchmark()
m30.columns=['M30']
HPI = HPI_Bench.join(m30)
print(HPI.head())

print(HPI.corr())

state_HPI_M30 = HPI_data.join(m30)
print(state_HPI_M30.corr())

print(state_HPI_M30.corr()['M30'])

    

AttributeError: 'function' object has no attribute 'resample'

In [ ]:
## Start of 